# Imports

In [1]:
import transformers
from transformers import CLIPConfig, CLIPModel, CLIPProcessor, CLIPImageProcessor, CLIPTokenizerFast
import torch
import torch.nn as nn
import torch.nn.functional as F
import torch.optim.lr_scheduler as lr_scheduler
import numpy as np
import random
import math
import scipy.io as sio
import nibabel as nib
from pathlib import Path
from gensim.models import Word2Vec
import re

In [2]:
device = 'cuda' if torch.cuda.is_available() else 'cpu'
print(device)

cuda


# Load word and fMRI data

### Load 3d fMRI data

In [3]:
NUM_SUBJS = 8
subjects_fmri = [] #stores all 8 subject fmri np arrays

fMRI_folder = Path('./doi_10.5061_dryad.gt413__v1')
assert fMRI_folder.exists(), f"Foldder: {fMRI_folder} does not exist."

for subj_id in range(8):
#     fmri_file_name = str(subj_id) + '_masked_2d.npy'
#     fmri = np.load(fMRI_folder / fmri_file_name)  
    fmri_file_name = str(subj_id) + '_smooth_nifti_4d.nii'
    fmri = nib.load(fMRI_folder / fmri_file_name)
    fmri = np.array(fmri.dataobj)
    assert isinstance(fmri, np.ndarray), f"Imported fmri_scan for subject {subj_id} is not of type numpy.ndarray"
    assert(fmri.ndim) == 4, f"Imported fmri_scan for subject {subj_id} is not 4 dimensional"
    subjects_fmri.append(fmri)

# Load words

In [4]:
feature_matrix = np.zeros((5176,195)) #stores the feature vectors as a row for each word
feature_names = [] #stores the names of all features in order
feature_types = {} #stores the types of features and all the names of the features for each type

features = sio.loadmat(fMRI_folder / 'story_features.mat')
feature_count = 0
for feature_type in features['features'][0]:
    feature_types[feature_type[0][0]] = []
    if isinstance(feature_type[1][0], str):
        feature_types[feature_type[0][0]].append(feature_type[1][0])
        feature_names.append(feature_type[1][0])
    else:
        for feature in feature_type[1][0]:
            feature_types[feature_type[0][0]].append(feature[0])
            feature_names.append(feature[0])
    feature_matrix[:, feature_count:feature_count+feature_type[2].shape[1]] = feature_type[2] #adds the (5176xN) feature values to the feature matrix for the current feature group
    feature_count += feature_type[2].shape[1]

In [5]:
words_info = [] #stores tuples of (word, time, features) sorted by time appeared

mat_file = fMRI_folder / 'subject_1.mat' #only looks at the first subject file, somewhere it said all the timings were the same so this should be safe
mat_contents = sio.loadmat(mat_file)
for count, row in enumerate(mat_contents['words'][0]):
    word_value = row[0][0][0][0]
    time = row[1][0][0]
    word_tuple = (word_value, time, feature_matrix[count,:])
    words_info.append(word_tuple)

In [6]:
chapter_nine_text = ""
for row in mat_contents['words'][0]:
    chapter_nine_text += row[0][0][0][0] + " "
print(chapter_nine_text)

Harry had never believed he would meet a boy he hated more than Dudley, but that was before he met Draco Malfoy. Still, first-year Gryffindors only had Potions with the Slytherins, so they didn't have to put up with Malfoy much. Or at least, they didn't until they spotted a notice pinned up in the Gryffindor common room that made them all groan. Flying lessons would be starting on Thursday -- and Gryffindor and Slytherin would be learning together. + "Typical," said Harry darkly. "Just what I always wanted. To make a fool of myself on a broomstick in front of Malfoy." + He had been looking forward to learning to fly more than anything else. "You don't know that you'll make a fool of yourself," said Ron reasonably. "Anyway, I know Malfoy's always going on about how good he is at Quidditch, but I bet that's all talk." + Malfoy certainly did talk about flying a lot. He complained loudly about first years never getting on the House Quidditch teams and told long, boastful stories that alway

### Align fMRI scans with sets of 4 words

In [7]:
subjects_samples = [[] for i in range(NUM_SUBJS)] #stores lists of all the samples for each subject

word_count = 0
while word_count < len(words_info) - 8:
    #gets the 4 input words, and the 4 consecutive words while verifying they were read in sequence
    scan_words = []
    start_time = words_info[word_count][1]
    in_sequence = True #tracks if the words are in sequence or not
    for i in range(8):
        word_info = words_info[word_count + i]
        if word_info[1] != start_time + 0.5*i:
            #if some of the words are not in sequence, skip forward 1 word after innter loop
            in_sequence = False
        scan_words.append(word_info[0])
    if not in_sequence:
        word_count +=1
        continue
    fmri_time = start_time + 2 #effect of reading words is assumed to start 2 seconds after and end 8 seconds after
    fmri_index = fmri_time//2 #since a scan happens every two seconds, the index is the time divided by 2
    if not isinstance(fmri_index, np.int32):
        #if the first word is not aligned with the fmri scan (i.e. its not the first word in a TR)
        word_count += 1
        continue
    for count, subject in enumerate(subjects_fmri):
        #adds tuple of (fmri_scan, four words)
        subjects_samples[count].append((subject[:,:,:,fmri_index+2], scan_words[0:4]))
    print("Created sample:")
    print("\tScan time:", str(start_time))
    print("\tInput words:", str(scan_words[0:4]))
    #if successful, skip forward to the next set of 4 words
    word_count += 4

print("Total number of samples:", str(len(subjects_samples[0])))

Created sample:
	Scan time: 20
	Input words: ['Harry', 'had', 'never', 'believed']
Created sample:
	Scan time: 22
	Input words: ['he', 'would', 'meet', 'a']
Created sample:
	Scan time: 24
	Input words: ['boy', 'he', 'hated', 'more']
Created sample:
	Scan time: 26
	Input words: ['than', 'Dudley,', 'but', 'that']
Created sample:
	Scan time: 28
	Input words: ['was', 'before', 'he', 'met']
Created sample:
	Scan time: 30
	Input words: ['Draco', 'Malfoy.', 'Still,', 'first-year']
Created sample:
	Scan time: 32
	Input words: ['Gryffindors', 'only', 'had', 'Potions']
Created sample:
	Scan time: 34
	Input words: ['with', 'the', 'Slytherins,', 'so']
Created sample:
	Scan time: 36
	Input words: ['they', "didn't", 'have', 'to']
Created sample:
	Scan time: 38
	Input words: ['put', 'up', 'with', 'Malfoy']
Created sample:
	Scan time: 40
	Input words: ['much.', 'Or', 'at', 'least,']
Created sample:
	Scan time: 42
	Input words: ['they', "didn't", 'until', 'they']
Created sample:
	Scan time: 44
	Input w

	Input words: ['contact.', "What's", 'the', 'matter?']
Created sample:
	Scan time: 1462
	Input words: ['Never', 'heard', 'of', 'a']
Created sample:
	Scan time: 1464
	Input words: ["wizard's", 'duel', 'before,', 'I']
Created sample:
	Scan time: 1466
	Input words: ['suppose?"', '+', '"Of', 'course']
Created sample:
	Scan time: 1468
	Input words: ['he', 'has,"', 'said', 'Ron,']
Created sample:
	Scan time: 1470
	Input words: ['wheeling', 'around.', '"I\'m', 'his']
Created sample:
	Scan time: 1472
	Input words: ['second,', "who's", 'yours?"', '+']
Created sample:
	Scan time: 1474
	Input words: ['Malfoy', 'looked', 'at', 'Crabbe']
Created sample:
	Scan time: 1476
	Input words: ['and', 'Goyle,', 'sizing', 'them']
Created sample:
	Scan time: 1478
	Input words: ['up.', '+', '"Crabbe,"', 'he']
Created sample:
	Scan time: 1480
	Input words: ['said.', '"Midnight', 'all', 'right?']
Created sample:
	Scan time: 1482
	Input words: ["We'll", 'meet', 'you', 'in']
Created sample:
	Scan time: 1484
	Input 

# Text encoding

In [22]:
#https://radimrehurek.com/gensim/models/word2vec.html

In [8]:
with open("./J. K. Rowling - Harry Potter 1 - Sorcerer's Stone.txt") as file:
    data = file.read().replace('\n',' ')

sentence_tokens = []
#split by all periods not preceded by Mr or Mrs
for sentence in re.split("(?<!Mr)(?<!Mrs)\.($| )", data + " " + chapter_nine_text):
    sentence_tokens.append(sentence.split(" "))
print(sentence_tokens)

[['Harry', 'Potter', 'and', 'the', "Sorcerer's", 'Stone', '', '', 'CHAPTER', 'ONE', '', 'THE', 'BOY', 'WHO', 'LIVED', '', 'Mr.', 'and', 'Mrs.', 'Dursley,', 'of', 'number', 'four,', 'Privet', 'Drive,', 'were', 'proud', 'to', 'say', 'that', 'they', 'were', 'perfectly', 'normal,', 'thank', 'you', 'very', 'much'], ['', ''], ['They', 'were', 'the', 'last', 'people', "you'd", 'expect', 'to', 'be', 'involved', 'in', 'anything', 'strange', 'or', 'mysterious,', 'because', 'they', 'just', "didn't", 'hold', 'with', 'such', 'nonsense'], ['', ''], ['', 'Mr.', 'Dursley', 'was', 'the', 'director', 'of', 'a', 'firm', 'called', 'Grunnings,', 'which', 'made', 'drills'], ['', ''], ['He', 'was', 'a', 'big,', 'beefy', 'man', 'with', 'hardly', 'any', 'neck,', 'although', 'he', 'did', 'have', 'a', 'very', 'large', 'mustache'], ['', ''], ['Mrs.', 'Dursley', 'was', 'thin', 'and', 'blonde', 'and', 'had', 'nearly', 'twice', 'the', 'usual', 'amount', 'of', 'neck,', 'which', 'came', 'in', 'very', 'useful', 'as', '

In [9]:
word_vec_encoder = Word2Vec(sentences=sentence_tokens, vector_size=100, window=4, min_count=0)

In [98]:
vector = model.wv['Harry']
print(vector)
sims = model.wv.most_similar('Harry', topn=10)
print(sims)

[-0.1592762   1.0358157   0.3998281   0.65896773 -0.14341635 -1.1957458
  0.5335763   1.7380077  -0.766566   -1.0356336  -0.07566728 -1.1751062
  0.62940866  0.7446685   0.7535447  -0.9587012   0.8585927  -0.89001256
  0.47481298 -1.7392517   0.6873861   0.32204965  0.9817534   0.1653276
 -0.32936937  0.02548517 -0.7163936  -0.16398834 -0.2911528   0.2216895
  0.869124   -0.5320245   0.6003812  -0.835552   -0.5567736   0.8724841
 -0.03029839 -0.2978085  -0.02549259 -1.0850229   0.36631638 -0.8160902
 -0.8166265  -0.4492721   0.4768799  -0.79738665 -0.5776063  -0.12688905
  0.62858564  0.05322775  0.2809282  -0.36204645 -0.38997352 -0.03191327
 -0.06836174  0.18175007  0.15393417 -0.2835372  -0.5398434   0.4702249
 -0.497334    0.07764219  0.72429174  0.21869192 -1.058616    0.64307624
  0.26159742  0.47916225 -0.8020325   0.76346177 -0.2581009  -0.115255
  0.920842    0.13798098  0.83246446  0.07702633  0.33448848  0.49757266
 -0.69999015 -0.22959568 -0.7526406  -0.38327488 -0.01637377

In [99]:
vec = model.wv['+']
print(vec)
sims = model.wv.most_similar('+', topn=10)
print(sims)

[-0.11667868  0.8429349   0.32117662  0.53995454 -0.12214363 -0.95944095
  0.4410393   1.4363979  -0.6178511  -0.8422581  -0.05303952 -0.9375535
  0.45371264  0.6066769   0.5892294  -0.7796291   0.6357723  -0.73351073
  0.36776012 -1.4180871   0.5679081   0.28288183  0.79845035  0.17510816
 -0.24930765  0.00582835 -0.593178   -0.12943596 -0.23465817  0.16131814
  0.6633559  -0.41084656  0.49868703 -0.6812801  -0.44114894  0.7041934
 -0.01215455 -0.26742408 -0.04254748 -0.90935147  0.25611266 -0.6575219
 -0.64853936 -0.364395    0.40166733 -0.6193323  -0.47563508 -0.09127057
  0.49026     0.07301917  0.25201496 -0.27739495 -0.35510117 -0.04099831
 -0.05254434  0.11012886  0.13631187 -0.2566088  -0.46786755  0.3700717
 -0.42504042  0.0688227   0.58254904  0.11905532 -0.84944856  0.5287194
  0.251611    0.40147305 -0.64631826  0.6357761  -0.20978577 -0.06242826
  0.7103947   0.09084885  0.6857637   0.07578729  0.3179003   0.3954695
 -0.56217504 -0.18856771 -0.59203774 -0.28812164 -0.01278

In [7]:
tokenizer = torch.hub.load('huggingface/pytorch-transformers', 'tokenizer', 'bert-base-cased')
text_encoder = torch.hub.load('huggingface/pytorch-transformers', 'model', 'bert-base-cased').to(device)

Using cache found in C:\Users\Portable/.cache\torch\hub\huggingface_pytorch-transformers_main
Using cache found in C:\Users\Portable/.cache\torch\hub\huggingface_pytorch-transformers_main


In [8]:

test_text = "Draco Malfoy. Still, first-year"

# Tokenized input with special tokens around it (for BERT: [CLS] at the beginning and [SEP] at the end)
indexed_tokens = tokenizer.encode(test_text, add_special_tokens=False)
print(indexed_tokens)
print(len(indexed_tokens))

# Define sentence A and B indices associated to 1st and 2nd sentences (see paper)
#segments_ids = [0, 0, 0, 0, 0, 0, 0, 0, 1, 1, 1, 1, 1, 1, 1, 1]

# Convert inputs to PyTorch tensors
tokens_tensor = torch.tensor([indexed_tokens]).to(device)
print(tokens_tensor)
print(tokens_tensor.shape)

with torch.no_grad():
    print(text_encoder(tokens_tensor)['last_hidden_state'])
    print(text_encoder(tokens_tensor)['last_hidden_state'].shape)

[1987, 17312, 18880, 14467, 1183, 119, 4209, 117, 1148, 118, 1214]
11
tensor([[ 1987, 17312, 18880, 14467,  1183,   119,  4209,   117,  1148,   118,
          1214]], device='cuda:0')
torch.Size([1, 11])
tensor([[[ 0.2427,  0.2542,  0.3174,  ..., -0.5812,  0.2457, -0.0402],
         [-0.0625,  0.1290,  0.2033,  ..., -0.5730,  0.4792,  0.1508],
         [ 0.1854, -0.0772,  0.3786,  ..., -0.3806,  0.3886, -0.0047],
         ...,
         [-0.1498, -0.2543, -0.0726,  ..., -0.7107, -0.1733,  0.4407],
         [ 0.4777, -0.1650,  0.0273,  ..., -0.4016,  0.0094, -0.1742],
         [ 0.7020,  0.1362,  0.3621,  ..., -0.2534, -0.1503, -0.0344]]],
       device='cuda:0')
torch.Size([1, 11, 768])


### Replace words with tokenized versions

In [9]:
subject_0_tokenized = []
for sample in subjects_samples[0]:
    words = " ".join(sample[1])
    print(words)
    tokens = tokenizer.encode(words, add_special_tokens=False)
    print(tokens)
    subject_0_tokenized.append((sample[0], tokens))

Harry had never believed
[3466, 1125, 1309, 2475]
he would meet a
[1119, 1156, 2283, 170]
boy he hated more
[2298, 1119, 5687, 1167]
than Dudley, but that
[1190, 12840, 117, 1133, 1115]
was before he met
[1108, 1196, 1119, 1899]
Draco Malfoy. Still, first-year
[1987, 17312, 18880, 14467, 1183, 119, 4209, 117, 1148, 118, 1214]
Gryffindors only had Potions
[144, 1616, 16274, 8380, 1116, 1178, 1125, 18959, 6126]
with the Slytherins, so
[1114, 1103, 156, 1193, 8420, 4935, 117, 1177]
they didn't have to
[1152, 1238, 112, 189, 1138, 1106]
put up with Malfoy
[1508, 1146, 1114, 18880, 14467, 1183]
much. Or at least,
[1277, 119, 2926, 1120, 1655, 117]
they didn't until they
[1152, 1238, 112, 189, 1235, 1152]
spotted a notice pinned
[6910, 170, 4430, 11973]
up in the Gryffindor
[1146, 1107, 1103, 144, 1616, 16274, 8380]
common room that made
[1887, 1395, 1115, 1189]
them all groan. Flying
[1172, 1155, 13344, 119, 7769]
lessons would be starting
[8497, 1156, 1129, 2547]
on Thursday -- and
[1113, 

# Image encoding

In [23]:
#https://www.kaggle.com/code/schmoyote/simple-cnn-architecture-for-image-classification

In [10]:
class SimpleCNN(nn.Module):
    def __init__(self):
        super(SimpleCNN, self).__init__()
        self.relu = nn.ReLU()
        self.max_pool = nn.MaxPool3d(3)
        self.bn = nn.BatchNorm3d(1)
        self.conv1 = nn.Conv3d(1, 32, kernel_size = 3)
        self.conv2 = nn.Conv3d(32, 64, kernel_size = 3)
        self.conv3 = nn.Conv3d(64, 64, kernel_size = 3)
        
    def forward(self, x):
        out = self.bn(x)
        out = self.relu(self.conv1(x))
        out = self.max_pool(out)
        out = self.relu(self.conv2(out))
        out = self.max_pool(out)
        out = self.relu(self.conv3(out))
        out = out.view(out.size(0), -1)
        return out

In [11]:
class ResidualBlock(nn.Module):
    def __init__(self, in_channels, out_channels, stride = 1, downsample = None):
        super(ResidualBlock, self).__init__()
        self.conv1 = nn.Sequential(
                        nn.Conv3d(in_channels, out_channels, kernel_size = 3, stride = stride, padding = 1),
                        nn.ReLU())
        self.conv2 = nn.Sequential(
                        nn.Conv3d(out_channels, out_channels, kernel_size = 3, stride = 1, padding = 1))
        self.downsample = downsample
        self.relu = nn.ReLU()
        self.out_channels = out_channels
        
    def forward(self, x):
        residual = x
        out = self.conv1(x)
        out = self.conv2(out)
        if self.downsample:
            residual = self.downsample(x)
        out += residual
        out = self.relu(out)
        return out

In [12]:
#https://blog.paperspace.com/writing-resnet-from-scratch-in-pytorch/
class ResNet(nn.Module):
    def __init__(self, block, layers, num_classes = 10):
        super(ResNet, self).__init__()
        self.inplanes = 64
        self.conv1 = nn.Sequential(
                        nn.Conv3d(1, 64, kernel_size = 7, stride = 2, padding = 3),
                        nn.ReLU())
        self.maxpool = nn.MaxPool3d(kernel_size = 3, stride = 2, padding = 1)
        self.layer0 = self._make_layer(block, 64, layers[0], stride = 1)
        self.layer1 = self._make_layer(block, 128, layers[1], stride = 2)
        self.layer2 = self._make_layer(block, 256, layers[2], stride = 2)
        self.layer3 = self._make_layer(block, 512, layers[3], stride = 2)
        self.avgpool = nn.AvgPool3d(2, stride=1) #i changed 7 to 2
        self.fc = nn.Linear(512, num_classes)
        
    def _make_layer(self, block, planes, blocks, stride=1):
        downsample = None
        if stride != 1 or self.inplanes != planes:
            
            downsample = nn.Sequential(
                nn.Conv3d(self.inplanes, planes, kernel_size=1, stride=stride),
            )
        layers = []
        layers.append(block(self.inplanes, planes, stride, downsample))
        self.inplanes = planes
        for i in range(1, blocks):
            layers.append(block(self.inplanes, planes))

        return nn.Sequential(*layers)
    
    
    def forward(self, x):
        #print(x.shape)
        x = self.conv1(x)
        #print(x.shape)
        x = self.maxpool(x)
        #print(x.shape)
        x = self.layer0(x)
        #print(x.shape)
        x = self.layer1(x)
        #print(x.shape)
        x = self.layer2(x)
        #print(x.shape)
        x = self.layer3(x)
        #print(x.shape)

        x = self.avgpool(x)
        x = x.view(x.size(0), -1)
#         x = self.fc(x)

        return x

In [13]:
image_encoder = ResNet(ResidualBlock, [3, 4, 6, 3], num_classes=512).to(device)

# CLIP from scratch

In [14]:
def unison_shuffled_copies(a, b):
    assert len(a) == len(b)
    p = np.random.permutation(len(a))
    return a[p], b[p]

In [32]:
#clip model which simultaneously trains the text and image encoder as well as learning weights 
#for projecting encodings of both text and image to the same latent space

#model is based on psuedocode from original clip paper
class CLIP(nn.Module):
    def __init__(self, textEncoder, text_output_shape, imageEncoder, image_output_shape, embedding_dim):
        super(CLIP, self).__init__()
        #self.text_encoder = textEncoder(100, text_output_shape)
        self.text_output_shape = text_output_shape
        self.text_encoder = textEncoder
        self.text_proj = nn.Linear(text_output_shape, embedding_dim).to(device)
        #self.image_encoder = imageEncoder(1000, image_output_shape)
        self.image_output_shape = image_output_shape
        self.image_encoder = imageEncoder
        self.image_proj = nn.Linear(image_output_shape, embedding_dim).to(device)
    
    def forward(self, text, image):
        #gets encodings of text and images
#         text_features = self.text_encoder(text)
#         text_features = torch.zeros((len(text), self.text_output_shape))
        text_features = []
        for sample in text:
            sample_features = []
            for word in sample:
                stripped_word = re.sub("(?<!Mr)(?<!Mrs)\.($| )", "", word)
                sample_features += list(self.text_encoder.wv[stripped_word])
            text_features.append(sample_features)
        text_features = torch.tensor(text_features).float().to(device)
#         encodings = self.text_encoder(torch.tensor([sample]).to(device))['last_hidden_state']
#         text_features[idx] = torch.squeeze(torch.sum(encodings, dim=1), dim=0)
        image_features = self.image_encoder(torch.unsqueeze(torch.tensor(image).to(device), 1).float())
#         image_features = self.image_encoder(torch.reshape(torch.tensor(image).float().to(device), (image.shape[0], -1)))
#         image_features = torch.reshape(torch.tensor(image).float().to(device), (image.shape[0], -1))
    
        #projects text and images into latent space
        text_embed = self.text_proj(text_features)
        text_embed_norm = text_embed / text_embed.norm(dim=1, keepdim=True)
        image_embed = self.image_proj(image_features)
        image_embed_norm = image_embed/ image_embed.norm(dim=1, keepdim=True)
        
        #return text_embed_norm, image_embed_norm
        return text_embed, image_embed

In [43]:
#trains the clip model from scratch
def train_clip(model, text_samples, image_samples, batch_size=10, num_epochs=100, lr=1e-3, temp=0.07):
    #optimizer = torch.optim.Adam(model.parameters(), lr=lr, weight_decay=0.2)
    optimizer = torch.optim.SGD(model.parameters(), lr=lr)
#     scheduler = lr_scheduler.CosineAnnealingLR(optimizer, 1000)
    loss_fn = nn.CrossEntropyLoss()
    for epoch in range(num_epochs):
        print("\tLearning_rate:",optimizer.param_groups[0]["lr"])
        epoch_loss = 0
        epoch_correct = 0
        epoch_total = 0
#         text_samples, image_samples = unison_shuffled_copies(text_samples, image_samples)
        zipped = list(zip(image_samples, text_samples))
        random.shuffle(zipped)
        image_samples, text_samples = zip(*zipped)
        image_samples = np.array(image_samples)
        #print(image_samples.shape)
        for batch in range(math.floor(image_samples.shape[0]/batch_size)):
#             print("\tBatch:", batch, "/", math.floor(image_samples.shape[0]/batch_size))
            optimizer.zero_grad()
            #gets embeddings for text and image batches
            start_idx = batch*batch_size
            end_idx = (batch+1)*batch_size
            text_batch, image_batch = text_samples[start_idx:end_idx], image_samples[start_idx:end_idx]
            text_embed, image_embed = model(text_batch, image_batch)
            #computes pairwise cosine similarity between text and image embeddings
            #logits = torch.matmul(text_embed, image_embed.t()) * math.exp(temp)
            logits = torch.cdist(text_embed, image_embed) #euclidean distances
            print(logits)
            #symmetric loss function
            labels = torch.arange(batch_size).to(device)
            loss_text = loss_fn(logits, labels)
            loss_image = loss_fn(logits.t(), labels)
            loss = (loss_text + loss_image)/2
            loss.backward()
            epoch_loss += loss.item()
            optimizer.step()
            #print(optimizer.state_dict)
            #compute accuracy
#             probs = torch.softmax(logits, dim=0)
#             print(probs)
#             print(torch.max(probs))
            winners = torch.argmax(logits, dim=0)
            print(winners)
            print(labels)
            corrects = (winners == labels)
            total_correct = corrects.sum().float().item()
            epoch_correct += total_correct
            epoch_total += batch_size
#         scheduler.step()
        print("Epoch:", epoch, "Training Loss:", epoch_loss, "Training Accuracy:", epoch_correct/epoch_total)
#         for param in model.parameters():
#             print(torch.absolute(param.grad.data).sum())
#         for name, param in model.named_parameters():
#             if param.requires_grad:
#                 print(param.grad)
#                 print(name, param.data)

### Tests out CLIP with very basic data and encoders

In [17]:
class TestModel(nn.Module):
    def __init__(self, input_size, output_size):
        super(TestModel, self).__init__()
        self.linear = nn.Linear(input_size, output_size)
    
    def forward(self, samples):
        return self.linear(samples)

In [17]:
#trains a clip model on random input data

text = torch.rand((50, 100))
images = torch.rand((50, 1000))

text_encoder = TestModel
image_encoder = TestModel

temp=0.07
clip_model = CLIP(TestModel(100, 60), 60, TestModel(1000,200), 200, 50)

torch.autograd.set_detect_anomaly(True)
train_clip(clip_model, text, images, num_epochs=5, temp=temp)

	Learning_rate: 0.001


RuntimeError: Expected all tensors to be on the same device, but found at least two devices, cuda:0 and cpu! (when checking argument for argument mat1 in method wrapper_CUDA_addmm)

In [51]:
#assesses the performance of the trained clip model on the entire training set
loss_fn = nn.CrossEntropyLoss()

text_embed, image_embed = clip_model(text, images)
#computes pairwise cosine similarity between text and image embeddings
logits = torch.matmul(text_embed, image_embed.t()) * math.exp(temp)
#symmetric loss function
labels = torch.arange(test_text.shape[0])
loss_text = loss_fn(logits, labels)
loss_image = loss_fn(logits.t(), labels)
loss = (loss_text + loss_image)/2
#compute accuracy
probs = torch.softmax(logits, dim=0)
winners = torch.argmax(probs, dim=0)
corrects = (winners == labels)
total_correct = corrects.sum().float().item()
print("Training Loss:", loss.item(), "Training Accuracy:", total_correct/test_text.shape[0])

Training Loss: 3.085871696472168 Training Accuracy: 1.0


In [52]:
#assesses the performance of the trained clip model on a test set

loss_fn = nn.CrossEntropyLoss()

test_text = torch.rand((50, 100))
test_images = torch.rand((50, 1000))

text_embed, image_embed = clip_model(test_text, test_images)
#computes pairwise cosine similarity between text and image embeddings
logits = torch.matmul(text_embed, image_embed.t()) * math.exp(temp)
#symmetric loss function
labels = torch.arange(test_text.shape[0])
loss_text = loss_fn(logits, labels)
loss_image = loss_fn(logits.t(), labels)
loss = (loss_text + loss_image)/2
#compute accuracy
probs = torch.softmax(logits, dim=0)
winners = torch.argmax(probs, dim=0)
corrects = (winners == labels)
total_correct = corrects.sum().float().item()
print("Testing Loss:", loss.item(), "Testing Accuracy:", total_correct/test_text.shape[0])

Testing Loss: 3.9154810905456543 Testing Accuracy: 0.08


### Train using real fMRI and text data

In [17]:
def split_samples(samples):
    images = np.zeros([len(samples)] + list(samples[0][0].shape))
    text = []
    for idx, sample in enumerate(samples):
        images[idx] = sample[0]
        text.append(sample[1])
    return images, text

In [19]:
#make sure samples are all tensors and properly formatted before inputting to torch model
train_images = torch.zeros((len(subjects_samples[0]), subjects_samples[0][0][0].flatten().shape[0]))
train_text = torch.zeros((len(subjects_samples[0]), 4*100))
for idx, sample in enumerate(subjects_samples[0]):
    train_images[idx] = torch.tensor(sample[0].flatten())
    for word_idx, word in enumerate(sample[1]):
        stripped_word = re.sub("(?<!Mr)(?<!Mrs)\.($| )", "", word)
        train_text[idx, word_idx*100:(word_idx+1)*100] = torch.tensor(word_vec_encoder.wv[stripped_word])
train_images = train_images.float().to(device)
print("before max:", torch.max(train_images))
print("before min:", torch.min(train_images))
train_images -= train_images.min(1, keepdim=True)[0]
train_images /= train_images.max(1, keepdim=True)[0]
print("after max:", torch.max(train_images))
print("after min:", torch.min(train_images))
train_text = train_text.float().to(device)
print(train_images.shape)
print(train_text.shape)

before max: tensor(750.8578, device='cuda:0')
before min: tensor(-0.0949, device='cuda:0')
after max: tensor(1., device='cuda:0')
after min: tensor(0., device='cuda:0')
torch.Size([1287, 159000])
torch.Size([1287, 400])


In [21]:
train_split = 0.05
temp = 0.07

train_samples = subjects_samples[0][:int(len(subjects_samples[0])*train_split)]
train_images, train_text = split_samples(train_samples)
print("Train:")
print(len(train_text))
print(train_images.shape)

test_samples = subjects_samples[0][int(len(subjects_samples[0])*train_split):]
test_images, test_text = split_samples(test_samples)
print("Test:")
print(len(test_text))
print(test_images.shape)

Train:
64
(64, 53, 60, 50)
Test:
1223
(1223, 53, 60, 50)


In [171]:
print(train_images[0].flatten().shape)

(159000,)


In [44]:
# text_encoder = torch.hub.load('huggingface/pytorch-transformers', 'model', 'bert-base-cased').to(device)
# image_encoder = ResNet(ResidualBlock, [3, 4, 6, 3], num_classes=512).to(device)
text_encoder = word_vec_encoder
image_encoder = SimpleCNN().to(device)
#image_encoder = TestModel(train_images[0].flatten().shape[0],1024).to(device)
clip_model = CLIP(text_encoder, 4*100, image_encoder, 1152, 50)

In [45]:
train_clip(clip_model, train_text, train_images, batch_size=10, lr=1e-6, num_epochs=1000, temp=0.07)

	Learning_rate: 1e-06
tensor([[204.4028, 203.9049, 204.1459, 204.2730, 204.3450, 203.7423, 203.9562,
         203.8020, 203.5014, 204.2075],
        [204.5186, 204.0218, 204.2625, 204.3874, 204.4592, 203.8589, 204.0728,
         203.9180, 203.6172, 204.3225],
        [204.3156, 203.8184, 204.0591, 204.1852, 204.2578, 203.6552, 203.8698,
         203.7150, 203.4150, 204.1202],
        [204.3568, 203.8591, 204.1001, 204.2241, 204.2968, 203.6959, 203.9103,
         203.7543, 203.4533, 204.1594],
        [204.5398, 204.0446, 204.2851, 204.4107, 204.4835, 203.8808, 204.0958,
         203.9421, 203.6424, 204.3465],
        [204.4222, 203.9247, 204.1654, 204.2902, 204.3619, 203.7621, 203.9756,
         203.8205, 203.5195, 204.2252],
        [204.3257, 203.8297, 204.0709, 204.1964, 204.2710, 203.6649, 203.8818,
         203.7267, 203.4273, 204.1321],
        [204.4222, 203.9266, 204.1682, 204.2901, 204.3654, 203.7612, 203.9788,
         203.8220, 203.5215, 204.2267],
        [204.4247, 203.927

tensor([5, 5, 5, 5, 5, 5, 5, 5, 5, 5], device='cuda:0')
tensor([0, 1, 2, 3, 4, 5, 6, 7, 8, 9], device='cuda:0')
tensor([[203.7949, 204.1144, 204.2184, 203.9672, 204.0778, 203.2627, 203.9535,
         203.9403, 204.3383, 204.7593],
        [203.8488, 204.1674, 204.2700, 204.0198, 204.1302, 203.3156, 204.0060,
         203.9932, 204.3901, 204.8109],
        [203.8511, 204.1686, 204.2701, 204.0223, 204.1308, 203.3174, 204.0067,
         203.9951, 204.3905, 204.8117],
        [203.7532, 204.0730, 204.1763, 203.9254, 204.0359, 203.2208, 203.9114,
         203.8986, 204.2963, 204.7174],
        [203.9285, 204.2474, 204.3506, 204.1013, 204.2106, 203.3963, 204.0860,
         204.0737, 204.4705, 204.8927],
        [203.8103, 204.1271, 204.2287, 203.9816, 204.0892, 203.2767, 203.9654,
         203.9542, 204.3491, 204.7698],
        [203.7208, 204.0384, 204.1415, 203.8916, 204.0011, 203.1875, 203.8775,
         203.8651, 204.2616, 204.6811],
        [203.6376, 203.9571, 204.0609, 203.8110, 203.91

tensor([3, 3, 3, 3, 3, 3, 3, 3, 3, 3], device='cuda:0')
tensor([0, 1, 2, 3, 4, 5, 6, 7, 8, 9], device='cuda:0')
tensor([[204.5667, 204.1059, 204.1758, 203.8549, 204.0433, 204.1698, 203.7427,
         204.8625, 203.9787, 203.2270],
        [204.5339, 204.0708, 204.1422, 203.8220, 204.0063, 204.1331, 203.7064,
         204.8276, 203.9450, 203.1914],
        [204.4796, 204.0163, 204.0892, 203.7688, 203.9533, 204.0784, 203.6528,
         204.7733, 203.8903, 203.1366],
        [204.4719, 204.0094, 204.0797, 203.7596, 203.9444, 204.0721, 203.6445,
         204.7660, 203.8842, 203.1297],
        [204.4500, 203.9877, 204.0602, 203.7394, 203.9263, 204.0509, 203.6253,
         204.7450, 203.8608, 203.1085],
        [204.4988, 204.0368, 204.1095, 203.7883, 203.9758, 204.0999, 203.6747,
         204.7939, 203.9096, 203.1575],
        [204.2486, 203.7865, 203.8570, 203.5369, 203.7229, 203.8497, 203.4224,
         204.5432, 203.6608, 202.9065],
        [204.6391, 204.1776, 204.2495, 203.9284, 204.11

       grad_fn=<CdistBackward0>)
tensor([7, 7, 7, 7, 7, 7, 7, 7, 7, 7], device='cuda:0')
tensor([0, 1, 2, 3, 4, 5, 6, 7, 8, 9], device='cuda:0')
tensor([[203.7008, 204.0482, 204.1113, 204.1299, 204.1205, 203.5883, 203.2225,
         204.0295, 203.6957, 203.8611],
        [203.6825, 204.0301, 204.0923, 204.1117, 204.1018, 203.5675, 203.2013,
         204.0137, 203.6775, 203.8415],
        [203.6474, 203.9962, 204.0592, 204.0777, 204.0692, 203.5365, 203.1700,
         203.9786, 203.6436, 203.8092],
        [203.6447, 203.9919, 204.0542, 204.0736, 204.0629, 203.5286, 203.1623,
         203.9756, 203.6395, 203.8029],
        [203.6273, 203.9756, 204.0377, 204.0576, 204.0488, 203.5143, 203.1480,
         203.9590, 203.6229, 203.7875],
        [203.7137, 204.0619, 204.1253, 204.1434, 204.1346, 203.6026, 203.2365,
         204.0436, 203.7094, 203.8753],
        [203.6848, 204.0320, 204.0944, 204.1140, 204.1045, 203.5711, 203.2054,
         204.0137, 203.6791, 203.8438],
        [203.7177, 204

       grad_fn=<CdistBackward0>)
tensor([0, 0, 0, 0, 0, 0, 0, 0, 0, 0], device='cuda:0')
tensor([0, 1, 2, 3, 4, 5, 6, 7, 8, 9], device='cuda:0')
tensor([[205.0664, 204.5719, 203.5524, 205.2182, 204.0799, 204.9565, 203.7391,
         203.9603, 204.1038, 203.9410],
        [204.6155, 204.1214, 203.0998, 204.7672, 203.6265, 204.5051, 203.2870,
         203.5089, 203.6536, 203.4880],
        [204.7497, 204.2559, 203.2326, 204.9026, 203.7599, 204.6393, 203.4212,
         203.6438, 203.7880, 203.6232],
        [204.8228, 204.3308, 203.3088, 204.9754, 203.8348, 204.7137, 203.4975,
         203.7177, 203.8636, 203.6966],
        [204.8287, 204.3357, 203.3124, 204.9823, 203.8397, 204.7191, 203.5020,
         203.7240, 203.8685, 203.7027],
        [204.9838, 204.4923, 203.4689, 205.1370, 203.9954, 204.8746, 203.6586,
         203.8788, 204.0247, 203.8586],
        [204.9086, 204.4184, 203.3942, 205.0619, 203.9198, 204.7998, 203.5845,
         203.8039, 203.9511, 203.7831],
        [204.8529, 204

...

       grad_fn=<CdistBackward0>)
tensor([1, 1, 1, 1, 1, 1, 1, 1, 1, 1], device='cuda:0')
tensor([0, 1, 2, 3, 4, 5, 6, 7, 8, 9], device='cuda:0')
tensor([[186.4389, 186.7794, 186.6111, 186.1121, 186.3990, 186.3487, 186.7963,
         186.9203, 186.2902, 186.6907],
        [186.5143, 186.8500, 186.6821, 186.1861, 186.4713, 186.4230, 186.8672,
         186.9917, 186.3621, 186.7605],
        [186.5066, 186.8441, 186.6770, 186.1792, 186.4653, 186.4157, 186.8622,
         186.9863, 186.3568, 186.7561],
        [186.2508, 186.5916, 186.4219, 185.9235, 186.2097, 186.1599, 186.6072,
         186.7322, 186.1008, 186.5004],
        [186.3852, 186.7238, 186.5540, 186.0574, 186.3430, 186.2943, 186.7395,
         186.8633, 186.2334, 186.6331],
        [186.3862, 186.7220, 186.5560, 186.0584, 186.3435, 186.2941, 186.7411,
         186.8666, 186.2361, 186.6340],
        [186.4366, 186.7737, 186.6081, 186.1094, 186.3952, 186.3450, 186.7929,
         186.9191, 186.2881, 186.6859],
        [186.1247, 186

       grad_fn=<CdistBackward0>)
tensor([7, 7, 7, 7, 7, 7, 7, 7, 7, 7], device='cuda:0')
tensor([0, 1, 2, 3, 4, 5, 6, 7, 8, 9], device='cuda:0')
tensor([[186.4146, 186.4610, 186.1103, 186.8959, 186.6135, 186.4214, 186.5298,
         186.3547, 186.7722, 186.4941],
        [186.2349, 186.2764, 185.9275, 186.7124, 186.4303, 186.2383, 186.3472,
         186.1698, 186.5878, 186.3130],
        [186.4485, 186.4950, 186.1440, 186.9299, 186.6472, 186.4552, 186.5638,
         186.3884, 186.8060, 186.5277],
        [186.1004, 186.1420, 185.7938, 186.5789, 186.2961, 186.1042, 186.2124,
         186.0365, 186.4541, 186.1794],
        [186.3423, 186.3871, 186.0368, 186.8218, 186.5400, 186.3480, 186.4570,
         186.2801, 186.6979, 186.4215],
        [186.2474, 186.2918, 185.9422, 186.7296, 186.4449, 186.2533, 186.3602,
         186.1865, 186.6038, 186.3276],
        [186.2941, 186.3400, 185.9900, 186.7760, 186.4926, 186.3008, 186.4086,
         186.2346, 186.6519, 186.3741],
        [186.4552, 186

tensor([2, 2, 2, 2, 2, 2, 2, 2, 2, 2], device='cuda:0')
tensor([0, 1, 2, 3, 4, 5, 6, 7, 8, 9], device='cuda:0')
tensor([[186.2900, 186.5356, 187.3517, 186.5468, 186.6637, 186.0887, 187.0038,
         186.3828, 186.8532, 187.2804],
        [186.1367, 186.3808, 187.1978, 186.3920, 186.5089, 185.9355, 186.8500,
         186.2281, 186.6990, 187.1274],
        [186.2268, 186.4711, 187.2861, 186.4800, 186.5982, 186.0236, 186.9411,
         186.3181, 186.7912, 187.2178],
        [186.1279, 186.3741, 187.1893, 186.3844, 186.5026, 185.9256, 186.8426,
         186.2212, 186.6918, 187.1189],
        [186.2686, 186.5132, 187.3284, 186.5216, 186.6384, 186.0673, 186.9831,
         186.3607, 186.8324, 187.2595],
        [186.0872, 186.3327, 187.1471, 186.3415, 186.4603, 185.8841, 186.8023,
         186.1798, 186.6516, 187.0786],
        [186.2522, 186.4950, 187.3125, 186.5070, 186.6241, 186.0497, 186.9645,
         186.3420, 186.8148, 187.2426],
        [186.1462, 186.3903, 187.2057, 186.3987, 186.51

tensor([4, 4, 4, 4, 4, 4, 4, 4, 4, 4], device='cuda:0')
tensor([0, 1, 2, 3, 4, 5, 6, 7, 8, 9], device='cuda:0')
tensor([[186.7200, 186.2705, 186.4414, 186.3807, 187.2976, 186.6452, 186.2807,
         186.3031, 186.2393, 186.6530],
        [186.6682, 186.2196, 186.3899, 186.3287, 187.2460, 186.5937, 186.2286,
         186.2510, 186.1875, 186.6011],
        [186.8841, 186.4370, 186.6054, 186.5455, 187.4614, 186.8105, 186.4443,
         186.4663, 186.4042, 186.8175],
        [186.7192, 186.2727, 186.4424, 186.3811, 187.2975, 186.6461, 186.2800,
         186.3015, 186.2405, 186.6530],
        [186.6728, 186.2256, 186.3960, 186.3353, 187.2505, 186.6000, 186.2334,
         186.2553, 186.1945, 186.6073],
        [186.6142, 186.1675, 186.3372, 186.2767, 187.1917, 186.5420, 186.1741,
         186.1966, 186.1357, 186.5489],
        [186.3840, 185.9366, 186.1078, 186.0456, 186.9622, 186.3113, 185.9440,
         185.9667, 185.9049, 186.3181],
        [186.7628, 186.3134, 186.4839, 186.4235, 187.34

KeyboardInterrupt: 